---
CSC 268 Homework #4: Optical Character Recognition via Morphology
---

Scanning a document produces an image of that document, represented as an array of pixels.  While written information may be present in the image, it is not explicitly represented as such, and cannot easily be searched or indexed in such a form.  Optical Character Recognition (OCR) refers to the ability to detect and extract the letters and other characters present in an image of a document so as to produce a transcription of the text therein.  Many approaches to OCR have been proposed over the years.  The one we will attempt in this homework is a relatively straightforward application of the moprphology tools we have been studying.  It can achieve reasonable success under ideal conditions:  when the text in the target document matches the provided templates closely in font and size.

In [ ]:
import cv2 as cv
import numpy as np
from scipy.ndimage import label
from scipy.spatial import distance_matrix
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap, LinearSegmentedColormap
from skimage.measure import regionprops, regionprops_table
from skimage.morphology import (erosion, dilation, closing, opening, skeletonize, thin, disk)
import matplotlib as mpl
mpl.rc('image', cmap='gray')

def imshow(img,cmap=None):
    plt.imshow(img)
    plt.axis('off')
    if cmap:
        plt.set_cmap(cmap)
    plt.show()

Below is a sample text we can try to recognize.  It has a simple monospaced font and bold characters.

In [ ]:
text = cv.imread('bold.png',0).astype(np.float32)/255.0
imshow(text)
tb = text < 0.5  # binarized text

We can apply our connected components labeling technique to identify individual letters.  A quick look at the results reveals a few problems:  Some of the components are non-letter characters like punctuation.  The lower-case i and j are actually two components each.  More subtly, because the labeling method applies labels in raster scan order, taller characters are numbered out of sequence with the shorter letters surrounding them.  You can see this in the different colorings in the visualization below.  The character 'd' in dog is label 15, right before the capital 'T' which is label 16.

In [ ]:
def show_labels(lbl,nlbl=None,cmap='rainbow'):
    cmap = mpl.colormaps[cmap]
    cmap.set_under(color="black")
    plt.imshow(lbl,cmap=cmap,interpolation='none',vmin=1,vmax=nlbl)
    plt.axis('off')
    plt.show()
    
lbl,nlbl = label(tb,structure=np.ones((3,3)))
print(lbl.max(),nlbl)
show_labels(lbl[:60])
imshow(lbl[:60]==15)
imshow(lbl[:60]==16)

### Part One: Label By Rows

We can deal with most of these problems via morphological techniques.  The implementation of a function to do so is actually tricky in a number of different ways.  Since we have bigger fish to fry (hello, OCR!) a solution to this part of the task appears below.  It relies on morphology in several places.  Your task for this part of the homework is to evaluate the code and understand how the morphological operations are being applied.  Please answer the questions that appear below.

1. What is the purpose of the first call to `regionprops`?
2. Why does `regionprops` need to be called a second time?
3. What is the purpose of the `dilation` call?  Explain the unusual structuring element.
4. Why do we need the centroids of the components?
5. What does one iteration of the loop achieve?
6. What are the contents of `relbl` as computed within the loop?
7. What does the line `lbl = relbl[lbl]` achieve?

In [ ]:
def labelByRows(b,minsize=-1,se=np.ones((3,3))):
    lbl,nlbl = label(b,se)
    
    # first filter out regions below the minimum area
    rgn = regionprops(lbl)
    area = np.array([cc.area for cc in rgn])
    big = (area>minsize)
    newlbl = np.append(0,np.cumsum(big)*big)  # zero at beginning is for background component
    #print(newlbl,nlbl)
    lbl = newlbl[lbl]
    rgn = regionprops(lbl)  # do this again since we've changed the labels
    nlbl = newlbl.max()
    #show_labels(lbl)
    #print(nlbl)
    
    # now identify rows and sort regions left to right within rows
    b2 = dilation(b,np.ones((1,2*b.shape[1])))
    lbl2,nlbl2 = label(b2)
    cx = np.array([cc.centroid[1] for cc in rgn])
    #print("cx",cx)
    relbl = np.zeros(nlbl+1,dtype=np.int32)  # +1 for background
    for i in range(1,nlbl2+1):
        rowlbl = np.unique(lbl[lbl2==i])
        rowlbl = rowlbl[rowlbl!=0]  # ignore the background
        order = np.argsort(np.argsort(cx[rowlbl-1]))  # -1 because cx doesn't include background
        # double argsort tells us where each item moves to in the sorted version
        #print("order",order)
        relbl[rowlbl] = rowlbl[order]
        #print("relbl",relbl)
    lbl = relbl[lbl]
    #show_labels(lbl)
    return lbl,nlbl
                  
tlbl,ntlbl = labelByRows(tb,14)
show_labels(tlbl)

### Part 2: Template Matching

Our first attempt at OCR will employ a simple template match.  To make this practical, we will need examples of each of the letter forms to be recognized.  Here is a second text image containing both cases of all letters of the alphabet.  For evaluation purposes, it will also be useful to know what the text in our original image should be if recognized successfully.

In [ ]:
# template image
alpha = cv.imread('alpha.png',0).astype(np.float32)/255.0
#imshow(alpha)
ab = alpha < 0.5
albl,nalbl = labelByRows(ab,14)
show_labels(albl)
atag = list('abcdefghijklmnopqrstuvwxyzABCDEFGHIJKLMNOPQRSTUVWXYZ')

# ground truth text
text = """Pangram 
The quick brown fox jumps over a lazy dog.

The New Colossus
By Emma Lazarus
Not like the brazen giant of Greek fame,
With conquering limbs astride from land to land;
Here at our sea-washed, sunset gates shall stand
A mighty woman with a torch, whose flame
Is the imprisoned lightning, and her name
Mother of Exiles. From her beacon-hand
Glows world-wide welcome; her mild eyes command
The air-bridged harbor that twin cities frame.
“Keep, ancient lands, your storied pomp!” cries she
With silent lips. “Give me your tired, your poor,
Your huddled masses yearning to breathe free,
The wretched refuse of your teeming shore.
Send these, the homeless, tempest-tost to me,
I lift my lamp beside the golden door!”"""
print(len(text))
letters = [c for c in list(text) if (ord(c)>=65 and ord(c)<=90) or (ord(c)>=97 and ord(c)<=122)]
print(len(letters))
print(letters)

The basic idea behind template matching is this:  erode the target text using a custom structuring element ('footprint') that is shaped like the character to be recognized.  Any pixels that remain following this operation represent a match for the template, by the definition of the erode operation.  (Can you see why?)  

Your first step for this part of the homework is to process the alphabet image into a list of individual templates, one for each character.  (The bounding box and/or image region properties will likely be useful here.) To make the matching process a little more robust, you should use just the skeleton of each character as the template.  Even so, the templates may not exactly match all examples of the character, and in some cases we will match portions of other characters.  

In [ ]:
# TODO:  Process alpha image to create individual letter templates.  Display some of them (at least 3).

Once you have your templates, try applying some of them using the `erosion` function.  You can apply `np.nonzero` to the result to get the coordinates of all the matched points.  A simple plotting function can then show us where the matches lie.

In [ ]:
def plotHits(hi,hj,img):
    '''Plot the locations of template hits, given their coordinates and the underlying image'''
    plt.imshow(img)
    plt.axis('off')
    plt.plot(hj,hi,'r+')
    plt.show()
    
# TODO: Use the function above to show all the matches for a few of your templates (at least 3).

This is nice, but not very complete.  To perform useful OCR, we need to systematically match every template against the entire image, and record for every match the corresponding component.  If more than one template matches to a single component, we will break ties by looking at the total number of pixels in the template.  Bigger templates represent a more complete match -- thus 'c is less complete than 'o', which in turn is less complete than 'p'.  If no templates match to a particular component, we will leave it blank for now.

For this portion of the assignment you will write a function that takes a label image, and a list of templates.  (The number of labels may also be specified as an optional/named argument, to save the trouble of computing it.)  Your function should return a vector with length equal to the number of components, where each element contains the index of the template that gave the most complete match.  Unmatched components will use the value `None`.

Depending on the shape of the template, the point where its center matches may or may not actually be a part of the letter image.  The `footprintOffset` function below gives the adjustment that will take a template match to an actual character pixel.

In [ ]:
def footprintOffset(foot):
    '''Figures out the offset between the footprint center and an active point'''
    (fi,fj) = erosion(foot,foot).nonzero()
    (ai,aj) = foot.nonzero()
    return(ai[ai.size//2]-fi,aj[aj.size//2]-fj)

# TODO: write a function to systematically apply all templates to a label image as described above.
# Call your function first with the alphabet image as a test -- every letter should match.
# Then apply it to the larger text image.

We can analyze the results in several ways.  One simple visualization simply displays the recognized characters on top of the text image.  Use this to look at your results.

If we want to be quantitative, we can compare the number of mistakes -- missing, incorrect, or extra labels.  The second function below uses the Levenshtein distance on strings to compute this value and report a result.  Run this on your results to see the score.  My first attempt got something over 70% of the letters correct.  While that's more than half, it still means that most words contain an error somewhere!

In [ ]:
def visualize(match,loc,img):
    '''Shows the matches for each component, the component centroids, and the original image'''
    plt.imshow(img)
    #print(match[1],match[2],match[3])
    for i in range(match.shape[0]):
        #print("one",i,match[i],loc[i,1]-5,loc[i,0]-5,atag[match[i]])
        if match[i]>=0:
            #print("two",i,match[i],loc[i,1]-5,loc[i,0]-5,atag[match[i]])
            plt.text(loc[i,1]-6,loc[i,0]-5,atag[match[i]],color='r')
    plt.axis('off')
    plt.show()

# TODO:  Apply the function above to your results.

In [ ]:
# from https://stackoverflow.com/questions/2460177/edit-distance-in-python:
def levenshteinDistance(s1, s2):
    if len(s1) > len(s2):
        s1, s2 = s2, s1

    distances = range(len(s1) + 1)
    for i2, c2 in enumerate(s2):
        distances_ = [i2+1]
        for i1, c1 in enumerate(s1):
            if c1 == c2:
                distances_.append(distances[i1])
            else:
                distances_.append(1 + min((distances[i1], distances[i1 + 1], distances_[-1])))
        distances = distances_
    return distances[-1]

def grade_transcription(s,gt):
    '''measures the number of errors in a transcription'''
    s2 = s.replace(" ","")
    gt2 = gt.replace(" ","")
    d = levenshteinDistance(s2,gt2)
    print(d,"errors in",len(gt2),"characters:",1-d/len(gt2),"% correct")
    
# TODO:  Apply the function above to your results.

If you want to try improving on your initial results, here are some ideas to try:
* Dilate the target components to make them slightly bigger.  This will make templates more likely to match.
* Resize the image to make everything twice as big.  This will give you more freedom to adjust the erosion of the templates, and/or the dilation of the mask.
* Try making the templates a little bigger to match the larger font size in the heading.

### Part Three: Statistical Component Matching

For this section you will try an alternative techniqe, also using morphological methods.  In this case, we will match characters based on statistics computed from the connected components.  In theory, each letter is consistent in shape so their statistical properties should be the same.  In practice ther eis some variation due to aliasing, etc.

The basic idea goes like this:  for each component, compute a vector of identifying statistics.  Do this for both the alphabet image and the target text.  Then, using Euclidean distance or some other metric, determine for each target character the template character with the most similar statistics vector.  This match will determine the component's label.  You can analyze the results using the same techniques as before.

What statistics should you use?  Take a look at the [scikit `regionprops` options](https://scikit-image.org/docs/stable/api/skimage.measure.html#skimage.measure.regionprops).  You only want measurements that don't depend on things that aren't dependent on the character type -- position, scale, etc.  In other words, you want translation and scale invariance (but not rotation invariance -- why?).  There are some packages of moments that have these properties.  You can also cook up your own, for example perimeter/area.  Also take a look at one-off properties like the Euler number.

In [ ]:
def nnclass(astat,tstat):
    '''returns the index of each t vector of the closest a vector'''
    d = distance_matrix(astat,tstat)  # args are MxK and NxK
    #print(d.shape)
    #imshow(d)
    return d.argmin(0).astype(np.int32)

# TODO:  Assemble two matrices of statistical properties, one for the alphabet templates and one for 
# the components in the text image.  They should have the same size in the second dimension.
# Call the function above to produce a match for each component.
# Evaluate the results using the methods from the previous section.

### Reflection

Record below your reflection on this assignment.  Which methods worked best, and why do you think that is?

What parts were hard? Surprising?  What did you learn from completing this assignment?

Please record the resources you consulted, and others in the class with whom you discussed the assignment.